# MetaSpore Getting Started

MetaSpore is a machine learning platform, which provides a one-stop solution for data preprocessing, model training and online prediction.

In this article, we introduce the basic API of MetaSpore briefly.

## Prepare Data

We use the publicly available dataset [Terabyte Click Logs](https://labs.criteo.com/2013/12/download-terabyte-click-logs-2/) published by CriteoLabs as our demo dataset.

We sample the dataset with sampling rate 0.001 so that the running of the demo can finish quickly. More information about the demo dataset can be found in [MetaSpore Demo Dataset](https://ks3-cn-beijing.ksyuncs.com/dmetasoul-bucket/demo/criteo/index.html).

Execute the following cell to download the demo dataset into the working directory. Those data files take up about 2.1 GiB disk space and the downloading process may take sveral minutes. If the downloading fails, please refer to [MetaSpore Demo Dataset](https://ks3-cn-beijing.ksyuncs.com/dmetasoul-bucket/demo/criteo/index.html) and download the dataset manually.

In [1]:
# import metaspore
# metaspore.demo.download_dataset()

You can check the downloaded dataset by executing the following cell.

In [2]:
!ls -l ${PWD}/data/

total 8
drwxrwxr-x 3 ec2-user ec2-user 4096 Jul  8 09:25 test
drwxrwxr-x 3 ec2-user ec2-user 4096 Jul  8 14:47 train


(Optional) To upload the dataset to your own s3 bucket:

1. Fill ``{YOUR_S3_BUCKET}`` and ``{YOUR_S3_PATH}`` with your preferred values in the following cell.
2. Uncomment the cell by removing the leading ``#`` character.
3. Execute the cell.

In [3]:
# YOUR_S3_BUCKET='s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/'
# YOUR_S3_PATH='datasets/CriteoLabs'

In [4]:
# !aws s3 cp --recursive ${PWD}/data/ s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/data/

Alternatively, you can open a terminal by selecting the ``File`` -> ``New`` -> ``Terminal`` menu item and executing Bash commands in it.

You can check the uploaded dataset in your s3 bucket by uncommenting and executing the following cell.

In [5]:
!aws s3 ls s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/data/

                           PRE test/
                           PRE train/


The ``schema`` directory contains configuration files and must also be uploaded to s3 so that the model can be trained in cluster environment. 

In [6]:
#!aws s3 cp --recursive ${PWD}/schema/ s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/schema/

In the rest of the article, we assume the demo dataset and schemas has been uploaded to `ROOT_DIR`.

In [7]:
ROOT_DIR = 's3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo'
# ROOT_DIR = '.'

## Define the Model

We can define our neural network model by subclassing ``torch.nn.Module`` as usual PyTorch models. The following ``DemoModule`` class provides an example.

Compared to usual PyTorch models, the notable difference is the ``_sparse`` layer created by instantiating ``ms.EmbeddingSumConcat`` which takes an embedding size and paths of two text files. ``ms.EmbeddingSumConcat`` makes it possible to define large-scale sparse models in PyTorch, which is a distinguishing feature of MetaSpore.

The ``_schema_dir`` field is an s3 directory which makes it possible to use the ``DemoModule`` class in cluster environment.

In [8]:
# import torch
# import metaspore as ms

# class DemoModule(torch.nn.Module):
#     def __init__(self):
#         super().__init__()
#         self._embedding_size = 16
#         self._schema_dir = ROOT_DIR + '/schema/'
#         self._column_name_path = self._schema_dir + 'column_name_demo.txt'
#         self._combine_schema_path = self._schema_dir + 'combine_schema_demo.txt'
#         self._sparse = ms.EmbeddingSumConcat(self._embedding_size, self._column_name_path, self._combine_schema_path)
#         self._sparse.updater = ms.FTRLTensorUpdater()
#         self._sparse.initializer = ms.NormalTensorInitializer(var=0.01)
#         self._dense = torch.nn.Sequential(
#             ms.nn.Normalization(self._sparse.feature_count * self._embedding_size),
#             torch.nn.Linear(self._sparse.feature_count * self._embedding_size, 1024),
#             torch.nn.ReLU(),
#             torch.nn.Linear(1024, 512),
#             torch.nn.ReLU(),
#             torch.nn.Linear(512, 1),
#         )

#     def forward(self, x):
#         x = self._sparse(x)
#         x = self._dense(x)
#         return torch.sigmoid(x)

In [9]:
import metaspore as ms
import torch
import torch.nn as nn


def nansum(x):
    return torch.where(torch.isnan(x), torch.zeros_like(x), x).sum()


def log_loss(yhat, y):
    return nansum(-(y * (yhat + 1e-12).log() + (1 - y) *
                    (1 - yhat + 1e-12).log()))

# 自定义的主函数入口
class DNNModelMain(nn.Module):
    def __init__(self, feature_config_file):
        super().__init__()
        self._embedding_size = 16
        self._schema_dir = ROOT_DIR + '/schema/'
        self._column_name_path = self._schema_dir + 'column_name_demo.txt'
        self._combine_schema_path = self._schema_dir + 'combine_schema_demo.txt'
        self.feature_config_file = feature_config_file  # TODO not used
        self._sparse = ms.EmbeddingSumConcat(
            self._embedding_size,
            combine_schema_source=self._column_name_path,
            combine_schema_file_path=self._combine_schema_path,
            # enable_feature_gen=True,
            # feature_config_file=feature_config_file,
            # enable_fgs=False
        )
        self._sparse.updater = ms.FTRLTensorUpdater(alpha=0.01)
        self._sparse.initializer = ms.NormalTensorInitializer(var=0.001)
        extra_attributes = {
            "enable_fresh_random_keep": True,
            "fresh_dist_range_from": 0, 
            "fresh_dist_range_to": 1000,
            "fresh_dist_range_mean": 950,
            "enable_feature_gen": True,
            "use_hash_code": False
        }
        self._sparse.extra_attributes = extra_attributes
        feature_count = self._sparse.feature_count
        feature_dim = self._sparse.feature_count * self._embedding_size

        self._gateEmbedding = GateEmbedding(feature_dim, feature_count, self._embedding_size)
        self._h1 = nn.Linear(feature_dim, 1024)
        self._h2 = FourChannelHidden(1024, 512)
        self._h3 = FourChannelHidden(512, 256)
        self._h4 = nn.Linear(256, 1)

        self._bn = ms.nn.Normalization(feature_dim, momentum=0.01, eps=1e-5, affine=True)
        self._zero = torch.zeros(1, 1)
        self.act0 = nn.Sigmoid()

    def forward(self, x):
        # print(f"self._sparse._data.type: {type(self._sparse._data)}, self._sparse._data.shape: {self._sparse._data.shape}, self._sparse._data: {self._sparse._data}") 
        print(f"x.type: {type(x)}, x.shape: {x.shape}, x: {x}")
        emb = self._sparse(x)
        print(f"emb.type: {type(emb)}, emb.shape: {emb.shape}, emb: {emb}")
        bno = self._bn(emb)
        print(f"bno.type: {type(bno)}, bno.shape: {bno.shape}, bno: {bno}")
        d = self._gateEmbedding(bno)
        o = self._h1(d)
        r, s1, s2, s3 = self._h2(o, self._zero, self._zero, self._zero)
        r, s1, s2, s3 = self._h3(r, s1, s2, s3)
        return self.act0(self._h4(r))


class FourChannelHidden(nn.Module):
    def __init__(self, in_size, out_size):
        super().__init__()
        self.wc2 = nn.Linear(int(in_size / 4), int(in_size / 4))
        self.wc3 = nn.Linear(int(in_size), int(in_size - in_size / 4 * 3))
        self.w = nn.Linear(int(in_size + int(in_size / 4) * 2) + int(in_size - int(in_size / 4) * 3) + 3, out_size)
        self.act1 = nn.Tanh()
        self.act = nn.ReLU()
        self.fl = int(in_size / 4)

    def forward(self, input, i1, i2, i3):
        f0 = input[:, :self.fl]
        f1 = input[:, self.fl:self.fl * 2]
        f2 = input[:, self.fl * 2:self.fl * 3]
        f3 = input[:, self.fl * 3:]

        c1 = self.act1(f0 * f1) * f1
        c2 = self.act1(self.wc2(f2) * f2)
        c3 = self.act1(f3 * self.wc3(input))

        s1 = torch.sum(c1, 1, True) + i1
        s2 = torch.sum(c2, 1, True) + i2
        s3 = torch.sum(c3, 1, True) + i3

        return self.act(self.w(torch.cat((input, c1, c2, c3, s1, s2, s3), 1))), s1, s2, s3


class GateEmbedding(nn.Module):
    def __init__(self, in_size, out_size, emb_size):
        super().__init__()
        self.layer1 = torch.nn.Linear(in_size, out_size)
        self.out_size = out_size
        self.emb_size = emb_size
        self.act2 = nn.Sigmoid()

    def forward(self, input):
        gate = self.act2(self.layer1(input))
        gate_reshape = torch.reshape(gate, (-1, self.out_size, 1))
        input_reshape = torch.reshape(input, (-1, self.out_size, self.emb_size))
        return (gate_reshape * input_reshape).reshape(-1, self.out_size * self.emb_size)

/home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/pyarrow/compute.py:196: RuntimeWarning: Python binding for StringBKDRHashFunctionOption not exposed
  warnings.warn("Python binding for {} not exposed"
/home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/pyarrow/compute.py:196: RuntimeWarning: Python binding for BKDRHashCombineFunctionOption not exposed
  warnings.warn("Python binding for {} not exposed"


Instantiating the ``DemoModule`` class to define our PyTorch model.

In [10]:
# module = DemoModule()
module = DNNModelMain('schema/combine_schema_demo.txt')

[WARN] 2024-07-09 06:53:52.126 STSAssumeRoleWithWebIdentityCredentialsProvider [140111453947712] Token file must be specified to use STS AssumeRole web identity creds provider.
[2024-07-09 06:53:52.131] [info] [s3_sdk_filesys.cpp:357] Try to open S3 stream: s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/schema/combine_schema_demo.txt, read_only true
[2024-07-09 06:53:52.155] [info] [s3_sdk_filesys.cpp:380] Opened read-only stream for object: s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/schema/combine_schema_demo.txt with total length 930
[2024-07-09 06:53:52.159] [info] [s3_sdk_filesys.cpp:419] Read S3 object s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/schema/combine_schema_demo.txt with size 930 at position 0 larger than total size: 930, change size to 930
[2024-07-09 06:53:52.182] [info] [s3_sdk_filesys.cpp:413] Read S3 object s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/schema/combine_schema_demo.txt reached end 

## Train the Model

To train our model, first we need to create a ``ms.PyTorchEstimator`` passing in several arguments including our PyTorch model ``module`` and the number of workers and servers.

``model_out_path`` specifies where to store the trained model.

``input_label_column_index`` specifies the column index of the label column in the dataset, which is ``0`` for the demo dataset.

In [11]:
model_out_path = ROOT_DIR + '/output/dev/model_out/'
estimator = ms.PyTorchEstimator(module=module,
                                worker_count=4,
                                server_count=4,
                                model_out_path=model_out_path,
                                experiment_name='0.1',
                                input_label_column_index=0)

Next, we create a Spark session by calling ``ms.spark.get_session()`` and load the training dataset by call ``ms.input.read_s3_csv()``.

``delimiter`` specifies the column delimiter of the dataset, which is the TAB character ``'\t'`` for the demo dataset.

We also need to pass column names because the csv files do not contain headers.

In [12]:
column_names = []
with open(f'./schema/column_name_demo.txt', 'r') as f:
    for line in f:
        column_names.append(line.split(' ')[1].strip())
print(column_names)

['label', 'integer_feature_1', 'integer_feature_2', 'integer_feature_3', 'integer_feature_4', 'integer_feature_5', 'integer_feature_6', 'integer_feature_7', 'integer_feature_8', 'integer_feature_9', 'integer_feature_10', 'integer_feature_11', 'integer_feature_12', 'integer_feature_13', 'categorical_feature_1', 'categorical_feature_2', 'categorical_feature_3', 'categorical_feature_4', 'categorical_feature_5', 'categorical_feature_6', 'categorical_feature_7', 'categorical_feature_8', 'categorical_feature_9', 'categorical_feature_10', 'categorical_feature_11', 'categorical_feature_12', 'categorical_feature_13', 'categorical_feature_14', 'categorical_feature_15', 'categorical_feature_16', 'categorical_feature_17', 'categorical_feature_18', 'categorical_feature_19', 'categorical_feature_20', 'categorical_feature_21', 'categorical_feature_22', 'categorical_feature_23', 'categorical_feature_24', 'categorical_feature_25', 'categorical_feature_26']


In [13]:
train_dataset_path = ROOT_DIR + '/data/train/day_0_0.001_train.csv'

spark_confs = {
    'spark.eventLog.enabled':'true',
    'spark.executor.memory': '20g',
    'spark.driver.memory': '10g',
}

spark_session = ms.spark.get_session(local=True,
                                     batch_size=100,
                                     worker_count=estimator.worker_count,
                                     server_count=estimator.server_count,
                                     log_level='INFO',
                                     spark_confs=spark_confs)
train_dataset = ms.input.read_s3_csv(spark_session, train_dataset_path, delimiter='\t', column_names=column_names)

24/07/09 06:53:53 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/07/09 06:53:55 INFO deprecation: fs.s3a.server-side-encryption-key is deprecated. Instead, use fs.s3a.server-side-encryption.key
24/07/09 06:53:55 INFO InMemoryFileIndex: It took 39 ms to list leaf files for 1 paths.


ignore shuffle


In [14]:
# train_dataset.count()

In [15]:
# train_dataset = train_dataset.limit(200000)

Finally, we call the ``fit()`` method of ``ms.PyTorchEstimator`` to train our model. This will take several minutes and you can see the progress by looking at the output of the cell. The trained model is stored in ``model_out_path`` and the ``model`` variable.

In [16]:
model = estimator.fit(train_dataset)

[2024-07-09 06:53:57.078] [info] PS job with coordinator address 172.16.14.249:45071 started.
[2024-07-09 06:53:57.078] [info] PSRunner::RunPS: pid: 30684, tid: 31373, thread: 0x7f6dfbf3f700
[2024-07-09 06:53:57.078] [info] PSRunner::RunPSCoordinator: pid: 30684, tid: 31373, thread: 0x7f6dfbf3f700
[2024-07-09 06:53:57.079] [info] ActorProcess::Receiving: Coordinator pid: 30684, tid: 31377, thread: 0x7f6df37fb700


24/07/09 06:53:57 INFO SparkContext: Starting job: collect at PythonRDD.scala:180
24/07/09 06:53:57 INFO SparkContext: Starting job: collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:308
24/07/09 06:53:57 INFO DAGScheduler: Got job 0 (collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:308) with 4 output partitions
24/07/09 06:53:57 INFO DAGScheduler: Final stage: ResultStage 0 (collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:308)
24/07/09 06:53:57 INFO DAGScheduler: Parents of final stage: List()
24/07/09 06:53:57 INFO DAGScheduler: Missing parents: List()
24/07/09 06:53:57 INFO DAGScheduler: Submitting ResultStage 0 (PythonRDD[3] at collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:308), which has no missing parents
24/07/09 06:53:57 INFO MemoryStore: Block broadcast_0 stored as values in memory

[2024-07-09 06:53:58.691] [info] C[0]:9: The coordinator has connected to 4 servers and 4 workers.
PS Coordinator node C[0]:9 is ready.


24/07/09 06:53:58 INFO Executor: Finished task 3.0 in stage 0.0 (TID 3). 1311 bytes result sent to driver
24/07/09 06:53:58 INFO Executor: Finished task 0.0 in stage 0.0 (TID 0). 1311 bytes result sent to driver
24/07/09 06:53:58 INFO Executor: Finished task 1.0 in stage 0.0 (TID 1). 1311 bytes result sent to driver
24/07/09 06:53:58 INFO Executor: Finished task 2.0 in stage 0.0 (TID 2). 1311 bytes result sent to driver
24/07/09 06:53:58 INFO TaskSchedulerImpl: Skip current round of resource offers for barrier stage 1 because the barrier taskSet requires 4 slots, while the total number of available slots is 1.
24/07/09 06:53:58 INFO TaskSchedulerImpl: Skip current round of resource offers for barrier stage 1 because the barrier taskSet requires 4 slots, while the total number of available slots is 2.
24/07/09 06:53:58 INFO TaskSchedulerImpl: Skip current round of resource offers for barrier stage 1 because the barrier taskSet requires 4 slots, while the total number of available slots 

2024-07-09 06:54:01.811 -- auc: 0.47111284001844167, Δauc: 0.47111284001844167, pcoc: 13.39133177863227, Δpcoc: 13.39133177863227, loss: 0.006607834815979004, Δloss: 0.006607834815979004, #instance: 1000
2024-07-09 06:54:01.819 -- auc: 0.43565838019207936, Δauc: 0.4008026718307093, pcoc: 13.20787947145227, Δpcoc: 13.029385334736592, loss: 0.006610182285308838, Δloss: 0.006612529754638672, #instance: 2000
2024-07-09 06:54:01.826 -- auc: 0.4635388486945581, Δauc: 0.5179478543964525, pcoc: 13.147843759710138, Δpcoc: 13.029394923029718, loss: 0.006609078089396159, Δloss: 0.006606869697570801, #instance: 3000
2024-07-09 06:54:01.833 -- auc: 0.47227069515330744, Δauc: 0.5102885928961749, pcoc: 14.390682391266324, Δpcoc: 20.087026119232178, loss: 0.006606305003166199, Δloss: 0.006597985744476318, #instance: 4000


...

self._sparse._data.type: <class 'torch.Tensor'>, self._sparse._data.shape: torch.Size([1755, 16]), self._sparse._data: tensor([[ 0.0072,  0.0031,  0.0056,  ..., -0.0087,  0.0000,  0.0097],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]],
       requires_grad=True)
x.type: <class 'torch.Tensor'>, x.shape: torch.Size([]), x: 0.0
emb.type: <class 'torch.Tensor'>, emb.shape: torch.Size([100, 656]), emb: tensor([[ 0.0072,  0.0031,  0.0056,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0014,  0.0010,  0.0024,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0037,  0.0039,  0.0013,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ..., -0.0005, -0.0017,

2024-07-09 06:54:42.060 -- auc: 0.6185818890479037, Δauc: 0.43452380952380953, pcoc: 1.688558073952813, Δpcoc: 0.4128246009349823, loss: 0.0016322253052158027, Δloss: 0.0073296369417853975, #instance: 195808
2024-07-09 06:54:42.114 -- auc: 0.6184453703671693, Δauc: 0.2785714285714286, pcoc: 1.68855135263853, Δpcoc: 1.6744097073872883, loss: 0.0016322540716940215, Δloss: 0.0016716436281070844, #instance: 195951
2024-07-09 06:54:42.121 -- auc: 0.6184573959445766, Δauc: 0.0, pcoc: 1.6886924785984383, Δpcoc: nan, loss: 0.0016321591997287604, Δloss: 0.0010124839842319488, #instance: 195981
2024-07-09 06:54:42.128 -- auc: 0.6185014267026243, Δauc: 0.6808943089430894, pcoc: 1.6887197817200232, Δpcoc: 1.7461928526560466, loss: 0.0016315801498630997, Δloss: 0.0009520425946412686, #instance: 196148


saving model to s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/
saving model to s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/
saving model to s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/
saving model to s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/
Get aws endpoint from env: 
[WARN] 2024-07-09 06:54:42.204 STSAssumeRoleWithWebIdentityCredentialsProvider [140258379134784] Token file must be specified to use STS AssumeRole web identity creds provider.
[2024-07-09 06:54:42.209] [info] [s3_sdk_filesys.cpp:357] Try to open S3 stream: s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/_sparse__sparse_meta.json, read_only false
Get aws endpoint from env: Get aws endpoint from env: 

[WARN] 2024-07-09 06:54:42.371 STSAssumeRoleWithWebIdentityCredentialsProvider [140257391539968] Token file must be specified t

[2024-07-09 06:54:50.455] [info] C[0]:9 has stopped.
[2024-07-09 06:54:50.458] [info] PS job with coordinator address 172.16.14.249:45071 stopped.


[WARN] 2024-07-09 06:54:50.371 STSAssumeRoleWithWebIdentityCredentialsProvider [140258379134784] Token file must be specified to use STS AssumeRole web identity creds provider.
[2024-07-09 06:54:50.374] [info] [s3_sdk_filesys.cpp:357] Try to open S3 stream: s3://sagemaker-us-west-2-452145973879/datasets/CriteoLabs/demo/output/dev/model_out/_bn.running_var__dense_data.dat, read_only false
24/07/09 06:54:50 INFO PythonRunner: Times: total = 8400, boot = -131, init = 133, finish = 8398
24/07/09 06:54:50 INFO PythonRunner: Times: total = 8400, boot = -131, init = 173, finish = 8358
24/07/09 06:54:50 INFO PythonRunner: Times: total = 8400, boot = -105, init = 147, finish = 8358
24/07/09 06:54:50 INFO PythonRunner: Times: total = 8400, boot = -131, init = 173, finish = 8358
24/07/09 06:54:50 INFO Executor: Finished task 3.0 in stage 16.0 (TID 71). 1311 bytes result sent to driver
24/07/09 06:54:50 INFO Executor: Finished task 0.0 in stage 16.0 (TID 68). 1311 bytes result sent to driver
24/07

## Evaluate the Model

To evaluate our model, we use the ``ms.input.read_s3_csv()`` function again to load the test dataset, passing in the column delimiter ``'\t'``.

In [17]:
test_dataset_path = ROOT_DIR + '/data/test/day_1_0.001_test.csv'
test_dataset = ms.input.read_s3_csv(spark_session, test_dataset_path, delimiter='\t', column_names=column_names)

[2024-07-09 06:54:50.500] [info] PS job with coordinator address 172.16.14.249:45071 stopped.
ps agent deregistered for process 31724 thread 0x7f9072dd7740
[2024-07-09 06:54:50.500] [info] PS job with coordinator address 172.16.14.249:45071 stopped.
ps agent deregistered for process 31725 thread 0x7f9072dd7740
[2024-07-09 06:54:50.500] [info] PS job with coordinator address 172.16.14.249:45071 stopped.
ps agent deregistered for process 31748 thread 0x7f9072dd7740
[2024-07-09 06:54:50.501] [info] PS job with coordinator address 172.16.14.249:45071 stopped.
ps agent deregistered for process 31743 thread 0x7f9072dd7740
24/07/09 06:54:50 INFO InMemoryFileIndex: It took 10 ms to list leaf files for 1 paths.


ignore shuffle


Next, we call the ``model.transform()`` method to transform the test dataset, which will add a column named ``rawPrediction`` to the test dataset representing the predicted labels. For ease of integration with Spark MLlib, ``model.transform()`` will also add a column named ``label`` to the test dataset representing the actual labels.

Like the training process, this will take several minutes and you can see the progress by looking at the output of the cell. The transformed test dataset is stored in the ``result`` variable.

In [18]:
result = model.transform(test_dataset)

[2024-07-09 06:54:50.725] [info] PS job with coordinator address 172.16.14.249:42453 started.
[2024-07-09 06:54:50.725] [info] PSRunner::RunPS: pid: 30684, tid: 819, thread: 0x7f6dde7f3700
[2024-07-09 06:54:50.725] [info] PSRunner::RunPSCoordinator: pid: 30684, tid: 819, thread: 0x7f6dde7f3700
[2024-07-09 06:54:50.727] [info] ActorProcess::Receiving: Coordinator pid: 30684, tid: 822, thread: 0x7f6df61fc700
[2024-07-09 06:54:50.754] [info] C[0]:9: The coordinator has connected to 4 servers and 4 workers.
PS Coordinator node C[0]:9 is ready.


24/07/09 06:54:50 INFO SparkContext: Starting job: collect at PythonRDD.scala:180
24/07/09 06:54:50 INFO DAGScheduler: Got job 17 (collect at PythonRDD.scala:180) with 4 output partitions
24/07/09 06:54:50 INFO DAGScheduler: Final stage: ResultStage 17 (collect at PythonRDD.scala:180)
24/07/09 06:54:50 INFO DAGScheduler: Parents of final stage: List()
24/07/09 06:54:50 INFO DAGScheduler: Missing parents: List()
24/07/09 06:54:50 INFO DAGScheduler: Submitting ResultStage 17 (PythonRDD[40] at RDD at PythonRDD.scala:53), which has no missing parents
24/07/09 06:54:50 INFO SparkContext: Starting job: collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:291
24/07/09 06:54:50 INFO MemoryStore: Block broadcast_19 stored as values in memory (estimated size 6.8 KiB, free 5.8 GiB)
24/07/09 06:54:50 INFO MemoryStore: Block broadcast_19_piece0 stored as bytes in memory (estimated size 4.2 KiB, free 5.8 GiB)
24/07/09 06:54:50 INFO BlockManagerInfo: Added

2024-07-09 06:54:56.380 -- auc: 0.7386824574389341, Δauc: 0.7386824574389341, pcoc: 0.9652412142072405, Δpcoc: 0.9652412142072405, loss: 0.001403188467025757, Δloss: 0.001403188467025757, #instance: 1000
2024-07-09 06:54:56.391 -- auc: 0.7093005801604635, Δauc: 0.6844476921203264, pcoc: 1.0717158628546672, Δpcoc: 1.1813221188152538, loss: 0.0014115914106369019, Δloss: 0.0014199943542480469, #instance: 2000
2024-07-09 06:54:56.400 -- auc: 0.7051703972304795, Δauc: 0.6982553891121666, pcoc: 1.071114060948196, Δpcoc: 1.0698927570791805, loss: 0.0014041462739308676, Δloss: 0.001389256000518799, #instance: 3000
2024-07-09 06:54:56.420 -- auc: 0.6984213984339465, Δauc: 0.6849193327864369, pcoc: 0.9829794496497852, Δpcoc: 0.7856345591337784, loss: 0.0014968813359737395, Δloss: 0.0017750865221023559, #instance: 4000


self._sparse._data.type: <class 'torch.Tensor'>, self._sparse._data.shape: torch.Size([1700, 16]), self._sparse._data: tensor([[ 0.0070,  0.0029,  0.0055,  ..., -0.0086,  0.0000,  0.0096],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]])
x.type: <class 'torch.Tensor'>, x.shape: torch.Size([]), x: 0.0
emb.type: <class 'torch.Tensor'>, emb.shape: torch.Size([100, 656]), emb: tensor([[0.0070, 0.0029, 0.0055,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        ...,
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0018, 0.0006, 0.0022,  ..., 0

2024-07-09 06:54:56.589 -- auc: 0.6949223828986062, Δauc: 0.6802088142334599, pcoc: 1.0346543735332703, Δpcoc: 1.300156568658763, loss: 0.0014508225679397582, Δloss: 0.0012665874958038331, #instance: 5000
2024-07-09 06:54:56.599 -- auc: 0.7006656922679062, Δauc: 0.736842105263158, pcoc: 1.0646953605578846, Δpcoc: 1.2371887699250252, loss: 0.0014224712053934733, Δloss: 0.0012807143926620483, #instance: 6000
2024-07-09 06:54:56.606 -- auc: 0.6972740153712307, Δauc: 0.6446428571428571, pcoc: 1.1206832150704995, Δpcoc: 1.7057562947273255, loss: 0.00136041659116745, Δloss: 0.0009880889058113099, #instance: 7000
2024-07-09 06:54:56.617 -- auc: 0.6937450213601903, Δauc: 0.6683400051652892, pcoc: 1.123745488024306, Δpcoc: 1.1456598788499832, loss: 0.0013606122955679893, Δloss: 0.0013619822263717652, #instance: 8000
2024-07-09 06:54:56.778 -- auc: 0.6977894535535627, Δauc: 0.7501921106557377, pcoc: 1.1622007102297063, Δpcoc: 1.580401251713435, loss: 0.0013268195721838209, Δloss: 0.0010564777851

...

self._sparse._data.type: <class 'torch.Tensor'>, self._sparse._data.shape: torch.Size([1783, 16]), self._sparse._data: tensor([[ 0.0064,  0.0034,  0.0064,  ..., -0.0083,  0.0000,  0.0110],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]])
x.type: <class 'torch.Tensor'>, x.shape: torch.Size([]), x: 0.0
emb.type: <class 'torch.Tensor'>, emb.shape: torch.Size([100, 656]), emb: tensor([[6.4496e-03, 3.4288e-03, 6.3605e-03,  ..., 0.0000e+00, 0.0000e+00,
         0.0000e+00],
        [7.0497e-03, 2.9373e-03, 5.4689e-03,  ..., 0.0000e+00, 0.0000e+00,
         0.0000e+00],
        [6.3750e-05, 0.0000e+00, 1.0243e-03,  ..., 0.0000e+00, 0.0000e+00,
         0.0000e+00],
        ...,
     

2024-07-09 06:55:06.721 -- auc: 0.674420956163609, Δauc: 0.6196261113140908, pcoc: 1.0978536271798423, Δpcoc: 0.9560052717433256, loss: 0.001360482665011902, Δloss: 0.0014567490816116333, #instance: 195732
2024-07-09 06:55:06.910 -- auc: 0.6748686061904707, Δauc: 0.7684450323339213, pcoc: 1.098219736307543, Δpcoc: 1.180345858846392, loss: 0.001359460656909967, Δloss: 0.0011594209671020508, #instance: 196732


emb.type: <class 'torch.Tensor'>, emb.shape: torch.Size([100, 656]), emb: tensor([[0.0070, 0.0029, 0.0055,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0070, 0.0029, 0.0055,  ..., 0.0000, 0.0000, 0.0000],
        ...,
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]])
bno.type: <class 'torch.Tensor'>, bno.shape: torch.Size([100, 656]), bno: tensor([[ 1.2769e+00,  5.4369e-01,  1.0404e+00,  ...,  9.5157e-03,
          1.4748e-03, -8.7526e-04],
        [-4.3628e-01, -2.9002e-01, -3.6653e-01,  ...,  9.5157e-03,
          1.4748e-03, -8.7526e-04],
        [ 1.2769e+00,  5.4369e-01,  1.0404e+00,  ...,  9.5157e-03,
          1.4748e-03, -8.7526e-04],
        ...,
        [-4.3628e-01, -2.9002e-01, -3.6653e-01,  ...,  9.5157e-03,
          1.4748e-03, -8.7526e-04],
        [-4.3628e-01, -2.9002

2024-07-09 06:55:07.085 -- auc: 0.6752030996687846, Δauc: 0.74348431593607, pcoc: 1.0970232968551774, Δpcoc: 0.8750133996500689, loss: 0.0013600165033738757, Δloss: 0.0014787491706243427, #instance: 197653
2024-07-09 06:55:07.245 -- auc: 0.6752030996687846, Δauc: 1.0, pcoc: 1.0970232968551774, Δpcoc: nan, loss: 0.0013600165033738757, Δloss: nan, #instance: 197653
2024-07-09 06:55:07.252 -- auc: 0.6750879798732254, Δauc: 0.6524466750313676, pcoc: 1.0961267784244877, Δpcoc: 0.9065728982289633, loss: 0.0013611605848121528, Δloss: 0.0016345960485603674, #instance: 198480
2024-07-09 06:55:07.259 -- auc: 0.6750549229906138, Δauc: 0.6660551965830687, pcoc: 1.096783991103958, Δpcoc: 1.278889052245928, loss: 0.0013608011342756867, Δloss: 0.0012734770920752312, #instance: 199297
2024-07-09 06:55:07.265 -- auc: 0.6750549229906138, Δauc: 1.0, pcoc: 1.096783991103958, Δpcoc: nan, loss: 0.0013608011342756867, Δloss: nan, #instance: 199297
[2024-07-09 06:55:07.274] [info] C[0]:9 has stopped.
[2024-07

24/07/09 06:55:07 INFO DataWritingSparkTask: Writer for partition 4 is committing.
24/07/09 06:55:07 INFO DataWritingSparkTask: Committed partition 4 (task 132, attempt 0, stage 31.0)
24/07/09 06:55:07 INFO Executor: Finished task 4.0 in stage 31.0 (TID 132). 2202 bytes result sent to driver
24/07/09 06:55:07 INFO TaskSetManager: Finished task 4.0 in stage 31.0 (TID 132) in 5655 ms on ip-172-16-14-249.us-west-2.compute.internal (executor driver) (8/8)
24/07/09 06:55:07 INFO TaskSchedulerImpl: Removed TaskSet 31.0, whose tasks have all completed, from pool 
24/07/09 06:55:07 INFO DAGScheduler: ResultStage 31 (collect at /home/ec2-user/anaconda3/envs/metaspore/lib/python3.8/site-packages/metaspore/agent.py:308) finished in 11.192 s
24/07/09 06:55:07 INFO DAGScheduler: Job 31 is finished. Cancelling potential speculative or zombie tasks for this job
24/07/09 06:55:07 INFO TaskSchedulerImpl: Killing all running tasks in stage 31: Stage finished
24/07/09 06:55:07 INFO DAGScheduler: Job 31 f

``result`` is a normal PySpark DataFrame and can be inspected by its methods.

In [19]:
result.show(5)

[2024-07-09 06:55:07.305] [info] PS job with coordinator address 172.16.14.249:42453 stopped.
ps agent deregistered for process 31748 thread 0x7f9072dd7740
[2024-07-09 06:55:07.313] [info] PS job with coordinator address 172.16.14.249:42453 stopped.
ps agent deregistered for process 31724 thread 0x7f9072dd7740
[2024-07-09 06:55:07.319] [info] PS job with coordinator address 172.16.14.249:42453 stopped.
ps agent deregistered for process 31743 thread 0x7f9072dd7740
[2024-07-09 06:55:07.327] [info] PS job with coordinator address 172.16.14.249:42453 stopped.
ps agent deregistered for process 31725 thread 0x7f9072dd7740


+-----------------+-----------------+-----------------+-----------------+-----------------+-----------------+-----------------+-----------------+-----------------+------------------+------------------+------------------+------------------+---------------------+---------------------+---------------------+---------------------+---------------------+---------------------+---------------------+---------------------+---------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+----------------------+-----+--------------------+
|integer_feature_1|integer_feature_2|integer_feature_3|integer_feature_4|integer_feature_5|integer_feature_6|integer_feature_7|integer_feature_8

24/07/09 06:55:07 INFO CodeGenerator: Code generated in 19.696161 ms
24/07/09 06:55:07 INFO SparkContext: Starting job: showString at NativeMethodAccessorImpl.java:0
24/07/09 06:55:07 INFO DAGScheduler: Got job 33 (showString at NativeMethodAccessorImpl.java:0) with 1 output partitions
24/07/09 06:55:07 INFO DAGScheduler: Final stage: ResultStage 33 (showString at NativeMethodAccessorImpl.java:0)
24/07/09 06:55:07 INFO DAGScheduler: Parents of final stage: List()
24/07/09 06:55:07 INFO DAGScheduler: Missing parents: List()
24/07/09 06:55:07 INFO DAGScheduler: Submitting ResultStage 33 (MapPartitionsRDD[81] at showString at NativeMethodAccessorImpl.java:0), which has no missing parents
24/07/09 06:55:07 INFO MemoryStore: Block broadcast_37 stored as values in memory (estimated size 49.9 KiB, free 5.8 GiB)
24/07/09 06:55:07 INFO MemoryStore: Block broadcast_37_piece0 stored as bytes in memory (estimated size 16.8 KiB, free 5.8 GiB)
24/07/09 06:55:07 INFO BlockManagerInfo: Added broadcast

Finally, we use ``pyspark.ml.evaluation.BinaryClassificationEvaluator`` to compute test AUC.

In [20]:
import pyspark
evaluator = pyspark.ml.evaluation.BinaryClassificationEvaluator()
test_auc = evaluator.evaluate(result)
print('test_auc: %g' % test_auc)

24/07/09 06:55:07 INFO CodeGenerator: Code generated in 4.352615 ms
24/07/09 06:55:07 INFO SparkContext: Starting job: sortByKey at BinaryClassificationMetrics.scala:189
24/07/09 06:55:07 INFO DAGScheduler: Registering RDD 90 (map at BinaryClassificationMetrics.scala:48) as input to shuffle 0
24/07/09 06:55:07 INFO DAGScheduler: Got job 34 (sortByKey at BinaryClassificationMetrics.scala:189) with 8 output partitions
24/07/09 06:55:07 INFO DAGScheduler: Final stage: ResultStage 35 (sortByKey at BinaryClassificationMetrics.scala:189)
24/07/09 06:55:07 INFO DAGScheduler: Parents of final stage: List(ShuffleMapStage 34)
24/07/09 06:55:07 INFO DAGScheduler: Missing parents: List(ShuffleMapStage 34)
24/07/09 06:55:07 INFO DAGScheduler: Submitting ShuffleMapStage 34 (MapPartitionsRDD[90] at map at BinaryClassificationMetrics.scala:48), which has no missing parents
24/07/09 06:55:07 INFO MemoryStore: Block broadcast_38 stored as values in memory (estimated size 43.7 KiB, free 5.8 GiB)
24/07/09

test_auc: 0.675057


24/07/09 06:55:09 INFO TaskSetManager: Starting task 0.0 in stage 44.0 (TID 181) (ip-172-16-14-249.us-west-2.compute.internal, executor driver, partition 0, NODE_LOCAL, 4271 bytes) taskResourceAssignments Map()
24/07/09 06:55:09 INFO TaskSetManager: Starting task 1.0 in stage 44.0 (TID 182) (ip-172-16-14-249.us-west-2.compute.internal, executor driver, partition 1, NODE_LOCAL, 4271 bytes) taskResourceAssignments Map()
24/07/09 06:55:09 INFO TaskSetManager: Starting task 2.0 in stage 44.0 (TID 183) (ip-172-16-14-249.us-west-2.compute.internal, executor driver, partition 2, NODE_LOCAL, 4271 bytes) taskResourceAssignments Map()
24/07/09 06:55:09 INFO TaskSetManager: Starting task 3.0 in stage 44.0 (TID 184) (ip-172-16-14-249.us-west-2.compute.internal, executor driver, partition 3, NODE_LOCAL, 4271 bytes) taskResourceAssignments Map()
24/07/09 06:55:09 INFO TaskSetManager: Starting task 4.0 in stage 44.0 (TID 185) (ip-172-16-14-249.us-west-2.compute.internal, executor driver, partition 4,

When all computations are done, we should call the ``stop()`` method of ``spark_session`` to make sure all the resources are released.

In [21]:
spark_session.stop()

24/07/09 06:55:09 INFO SparkUI: Stopped Spark web UI at http://ip-172-16-14-249.us-west-2.compute.internal:4040
24/07/09 06:55:09 INFO MapOutputTrackerMasterEndpoint: MapOutputTrackerMasterEndpoint stopped!
24/07/09 06:55:09 INFO MemoryStore: MemoryStore cleared
24/07/09 06:55:09 INFO BlockManager: BlockManager stopped
24/07/09 06:55:09 INFO BlockManagerMaster: BlockManagerMaster stopped
24/07/09 06:55:09 INFO OutputCommitCoordinator$OutputCommitCoordinatorEndpoint: OutputCommitCoordinator stopped!
24/07/09 06:55:09 INFO SparkContext: Successfully stopped SparkContext


## Summary

We illustrated how to train and evaluate neural network model in MetaSpore. Users familiar with PyTorch and Spark MLlib should get started easily, which is the design goal of MetaSpore.